In [1]:
%load_ext autoreload
%autoreload 2

from scripts.wandb_experiments.gr_comparison import ComparisonExperiment
import multiprocessing as mp
import torch
import wandb_util.wandb_util as wbu

torch.set_grad_enabled(False)
mp.set_start_method("spawn", force=True)

In [22]:
from scripts.wandb_experiments.gr_comparison import ComparisonExperimentConfig
from scripts.wandb_runs.run_generative_rendering import RunGenerativeRenderingConfig
from text3d2video.pipelines.generative_rendering_pipeline import (
    GenerativeRenderingConfig,
)
from text3d2video.pipelines.pipeline_utils import ModelConfig
from omegaconf import OmegaConf

decoder_paths = [
    "mid_block.attentions.0.transformer_blocks.0.attn1",
    "up_blocks.1.attentions.0.transformer_blocks.0.attn1",
    "up_blocks.1.attentions.1.transformer_blocks.0.attn1",
    "up_blocks.1.attentions.2.transformer_blocks.0.attn1",
    "up_blocks.2.attentions.0.transformer_blocks.0.attn1",
    "up_blocks.2.attentions.1.transformer_blocks.0.attn1",
    "up_blocks.2.attentions.2.transformer_blocks.0.attn1",
    "up_blocks.3.attentions.0.transformer_blocks.0.attn1",
    "up_blocks.3.attentions.1.transformer_blocks.0.attn1",
    "up_blocks.3.attentions.2.transformer_blocks.0.attn1",
]

base_config = RunGenerativeRenderingConfig(
    prompt="Deadpool, blank background",
    animation_tag="catwalk_180_20:latest",
    generative_rendering=GenerativeRenderingConfig(
        module_paths=decoder_paths,
    ),
    model=ModelConfig(),
    seed=0,
)
print(base_config)

num_keyframes = [1, 3, 5, 8, 10]
kf_seeds = [0, 1]

override_dims = [
    [{"generative_rendering.num_keyframes": n} for n in num_keyframes],
    [{"kf_seed": i} for i in range(2)],
]

override_dim_labels = [num_keyframes, kf_seeds]

exp_config = ComparisonExperimentConfig(
    base_config=OmegaConf.create(base_config),
    override_dims=override_dims,
    override_dim_labels=override_dim_labels,
)
exp_config = OmegaConf.create(exp_config)

e = ComparisonExperiment("180_kf_comparison", exp_config)

RunGenerativeRenderingConfig(prompt='Deadpool, blank background', animation_tag='catwalk_180_20:latest', generative_rendering=GenerativeRenderingConfig(module_paths=['mid_block.attentions.0.transformer_blocks.0.attn1', 'up_blocks.1.attentions.0.transformer_blocks.0.attn1', 'up_blocks.1.attentions.1.transformer_blocks.0.attn1', 'up_blocks.1.attentions.2.transformer_blocks.0.attn1', 'up_blocks.2.attentions.0.transformer_blocks.0.attn1', 'up_blocks.2.attentions.1.transformer_blocks.0.attn1', 'up_blocks.2.attentions.2.transformer_blocks.0.attn1', 'up_blocks.3.attentions.0.transformer_blocks.0.attn1', 'up_blocks.3.attentions.1.transformer_blocks.0.attn1', 'up_blocks.3.attentions.2.transformer_blocks.0.attn1'], do_pre_attn_injection=True, do_post_attn_injection=True, feature_blend_alpha=0.8, attend_to_self_kv=False, mean_features_weight=0.5, chunk_size=5, num_keyframes=1, num_inference_steps=10, guidance_scale=7.5, controlnet_conditioning_scale=1.0), model=ModelConfig(sd_repo='runwayml/stabl

In [38]:
e.specification()

[o_0([]),
 o_1([]),
 o_2([]),
 o_3([]),
 o_4([]),
 o_5([]),
 o_6([]),
 o_7([]),
 o_8([]),
 o_9([])]

In [44]:
e.sync_experiment(rerun_all=False)

Experiment up-to-date!


In [49]:
runs = e.get_runs_grouped()

In [50]:
import numpy as np
from text3d2video.artifacts.video_artifact import VideoArtifact
from text3d2video.utilities.video_util import pil_frames_to_clip

def get_video(run):
    video = wbu.logged_artifacts(run)[0]
    video = VideoArtifact.from_wandb_artifact(video)
    frames = video.read_frames()
    return pil_frames_to_clip(frames)

videos = np.vectorize(get_video)(runs)

In [51]:
from text3d2video.utilities.ipython_utils import display_vid
from text3d2video.utilities.video_comparison import video_grid


vids = video_grid(videos.T)

display_vid(vids, width=1000)